In [ ]:
import cv2
import mediapipe as mp
import numpy as np
import json
import os

mp_hands = mp.solutions.hands
hands = mp_hands.Hands(
    static_image_mode=False,
    max_num_hands=1,
    min_detection_confidence=0.8,
)
mp_drawing = mp.solutions.drawing_utils

def create_landmark(output_folder="data/landmarks_raw"):

    os.makedirs(output_folder, exist_ok=True)

    label = input("Add gesture name")

    cap = cv2.VideoCapture(0)
    count = 0

    while True:
        ret, frame = cap.read()
        if not ret:
            break

        frame_rgb = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
        result = hands.process(frame_rgb)

        if result.multi_hand_landmarks:
            for hand_landmarks in result.multi_hand_landmarks:
                # Рисуем точки на руке
                mp_drawing.draw_landmarks(frame, hand_landmarks, mp_hands.HAND_CONNECTIONS)

                # Извлекаем координаты
                landmarks = []
                for lm in hand_landmarks.landmark:
                    landmarks.extend([lm.x, lm.y, lm.z])

                # Сохраняем JSON
                data = {
                    "landmarks": landmarks,
                    "label": label
                }
                with open(f"data/landmarks_raw/{label}_{count}.json", "w") as f:
                    json.dump(data, f)
                count += 1

        cv2.imshow("Hand Capture", frame)
        if cv2.waitKey(1) & 0xFF == ord("q"):
            break

    cap.release()
    cv2.destroyAllWindows()


In [27]:
import cv2
import mediapipe as mp
import pandas as pd
import os

def extract_landmarks_to_csv(images_folder, output_csv, gesture_label):
    """
    Извлекает координаты 21 точки руки (x, y) из изображений в папке
    и сохраняет их в CSV в формате: x0,y0,x1,y1,...,x20,y20,gesture
    """

    mp_hands = mp.solutions.hands
    mp_drawing = mp.solutions.drawing_utils
    hands = mp_hands.Hands(
        static_image_mode=True,
        max_num_hands=1,
        min_detection_confidence=0.8,
    )

    rows = []
    not_found = []

    for filename in os.listdir(images_folder):
        if not filename.lower().endswith((".jpg", ".jpeg", ".png")):
            continue

        path = os.path.join(images_folder, filename)
        image = cv2.imread(path)

        if image is None:
            print(f"Не удалось прочитать {filename}")
            continue

        image_rgb = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)
        result = hands.process(image_rgb)

        if result.multi_hand_landmarks:
            hand_landmarks = result.multi_hand_landmarks[0]
            coords = []
            for lm in hand_landmarks.landmark:
                coords.extend([lm.x, lm.y])
            coords.append(gesture_label)
            rows.append(coords)
            print(f"Обработано: {filename}")
        else:
            not_found.append(filename)
            print(f"   Рука не найдена в {filename}")

    hands.close()
    cv2.destroyAllWindows()

    # Создаём DataFrame
    columns = [f"{axis}{i}" for i in range(21) for axis in ("x", "y")] + ["gesture"]
    df = pd.DataFrame(rows, columns=columns)

    # Создаём папку для CSV, если нет
    os.makedirs(os.path.dirname(output_csv), exist_ok=True)

    # Если файл существует и не пустой, добавляем к нему данные
    if os.path.exists(output_csv) and os.path.getsize(output_csv) > 0:
        existing = pd.read_csv(output_csv)
        df = pd.concat([existing, df], ignore_index=True)

    # Сохраняем CSV
    df.to_csv(output_csv, index=False, encoding="utf-8")

    print(f"\n  CSV сохранён: {output_csv} ({len(df)} строк)")
    if not_found:
        print(f"Не найдено рук в {len(not_found)} изображениях:")
        # for f in not_found:
        #     print("   -", f)


In [ ]:

output_csv = '../data/processed/if.csv'

if os.path.exists(output_csv):
    print("Файл существует")
else:
    print("Файл не найден")

In [ ]:

extract_landmarks_to_csv(images_folder='/home/fateee/Desktop/ulyana/hagrid/super_bolshoy_dataset/call', 
                         output_csv=output_csv, 
                         gesture_label='if')

In [ ]:
# dislike --> mafia

output_csv = '../data/processed/mafia.csv'

extract_landmarks_to_csv(images_folder='/home/fateee/Desktop/ulyana/hagrid/super_bolshoy_dataset/dislike', 
                         output_csv=output_csv, 
                         gesture_label='mafia')

In [ ]:
# like --> civilian

output_csv = '../data/processed/civilian.csv'

extract_landmarks_to_csv(images_folder='/home/fateee/Desktop/ulyana/hagrid/super_bolshoy_dataset/like', 
                         output_csv=output_csv, 
                         gesture_label='civilian')

In [ ]:
# ok --> sheriff

output_csv = '../data/processed/sheriff.csv'

extract_landmarks_to_csv(images_folder='/home/fateee/Desktop/ulyana/hagrid/super_bolshoy_dataset/ok', 
                         output_csv=output_csv, 
                         gesture_label='sheriff')

Новый метод для считывания координат и отметки какая это рука, для дальнейшего отзеркаливания


Структура csv будет выглядеть след образом: 

`x0, y0, x1, y1, ..., x20, y20, gesture, is_right_hand`


In [5]:
import cv2
import mediapipe as mp
import pandas as pd
import os

def extract_single_hand_to_csv(images_folder, output_csv, gesture_label):
    """
    Извлекает координаты одной руки из изображений и сохраняет в CSV.
    Столбцы: x0,y0,...,x20,y20,gesture,is_right_hand (1=Right, 0=Left)
    Также выводит статистику обработки изображений.
    """

    mp_hands = mp.solutions.hands
    hands = mp_hands.Hands(
        static_image_mode=True,
        max_num_hands=1,
        min_detection_confidence=0.8,
    )

    rows = []
    not_found = []
    total_images = 0

    for filename in os.listdir(images_folder):
        if not filename.lower().endswith((".jpg", ".jpeg", ".png")):
            continue

        total_images += 1
        img_path = os.path.join(images_folder, filename)
        image = cv2.imread(img_path)
        if image is None:
            print(f"Can't open file - {filename}")
            not_found.append(filename)
            continue

        image_rgb = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)
        result = hands.process(image_rgb)

        if result.multi_hand_landmarks and result.multi_handedness:
            
            hand_landmarks = result.multi_hand_landmarks[0]
            handedness_info = result.multi_handedness[0]

            is_right = 1 if handedness_info.classification[0].label == "Right" else 0

            coords = []
            for lm in hand_landmarks.landmark:
                coords.extend([lm.x, lm.y])

            row = coords + [gesture_label, is_right]
            rows.append(row)

            print(f"Done {filename}: {handedness_info.classification[0].label} рука")
        else:
            not_found.append(filename)
            print(f"   Hands are not found in {filename}")

    hands.close()
    cv2.destroyAllWindows()

    columns = [f"{axis}{i}" for i in range(21) for axis in ("x", "y")] + ["gesture", "is_right_hand"]
    df = pd.DataFrame(rows, columns=columns)

    os.makedirs(os.path.dirname(output_csv), exist_ok=True)

    if os.path.exists(output_csv) and os.path.getsize(output_csv) > 0:
        existing = pd.read_csv(output_csv)
        df = pd.concat([existing, df], ignore_index=True)

    df.to_csv(output_csv, index=False, encoding="utf-8")

    total_found = len(rows)
    success_rate = (total_found / total_images * 100) if total_images else 0

    print(f"\nCSV saved: {output_csv} ({len(df)} rows)")
    print(f"Total images processed: {total_images}")
    print(f"Images with detected hand(s): {total_found}")
    print(f"Images where no hand was detected: {len(not_found)}")
    print(f"Success rate: {success_rate:.1f}%")
    if not_found:
        print("Files with no detected hand:", not_found)



Извлекаем данные для 

In [6]:
# ok --> sheriff
output_csv = '../data/raw/sheriff.csv'

extract_single_hand_to_csv(images_folder='/home/fateee/Desktop/ulyana/hagrid/super_bolshoy_dataset/ok', 
                         output_csv=output_csv, 
                         gesture_label='sheriff')


I0000 00:00:1762253176.372022   47693 gl_context_egl.cc:85] Successfully initialized EGL. Major : 1 Minor: 5
I0000 00:00:1762253176.375873   82249 gl_context.cc:369] GL version: 3.2 (OpenGL ES 3.2 Mesa 25.0.7-0ubuntu0.24.04.1), renderer: AMD Radeon Graphics (radeonsi, renoir, ACO, DRM 3.61, 6.14.0-33-generic)
W0000 00:00:1762253176.439465   82233 inference_feedback_manager.cc:114] Feedback manager requires a model with a single signature inference. Disabling support for feedback tensors.
W0000 00:00:1762253176.503709   82242 inference_feedback_manager.cc:114] Feedback manager requires a model with a single signature inference. Disabling support for feedback tensors.


Done 3104ded2-df70-4833-8fc3-32c0cee9f4b1.jpg: Right рука
Done 30a45ec8-746a-445d-8318-88295eb5bb1a.jpg: Left рука
Done 0577e4fd-1a6f-409c-aeb6-286da6de5492.jpg: Left рука
Done eb457f7f-b0fc-4aa2-841b-164101804232.jpg: Left рука
Done c84ee6d2-a56a-4709-acb3-1b09aa824fad.jpg: Right рука
Done 4873fbf7-8d59-48ff-a92f-d8d431ed8725.jpg: Left рука
Done 34077929-7006-4fd4-bbde-1089a06de696.jpg: Right рука
Done 2b4c2ba2-0b27-4345-8d49-594d84a05d6f.jpg: Left рука
Done 7f7e4a0b-5f56-40b1-a2d7-3c41e74f5719.jpg: Left рука
Done a5d8118c-d319-4e76-958f-fa510660a752.jpg: Right рука
Done bf67ea77-1700-408b-a7b1-8fa4b37285af.jpg: Right рука
Done 0ee31f7a-d81b-4f4e-8d7f-a7286164777b.jpg: Right рука
Done 7a5cef69-eedf-49cf-93f0-688fd81831c0.jpg: Right рука
Done 3bec06f6-0cf5-4ace-a052-c4f86f70f8a5.jpg: Right рука
Done bb0ac0de-bbb2-43d0-8e18-ed69afac181a.jpg: Left рука
   Hands are not found in 202b19db-071d-4766-a79d-8202900d55ab.jpg
Done 1bfa7537-b2b2-4e65-91a1-7e4ad2159b79.jpg: Right рука
Done 12dbe6d

In [7]:
# call --> if
output_csv = '../data/raw/if.csv'

extract_single_hand_to_csv(images_folder='/home/fateee/Desktop/ulyana/hagrid/super_bolshoy_dataset/call', 
                         output_csv=output_csv, 
                         gesture_label='if')


I0000 00:00:1762258728.880190   47693 gl_context_egl.cc:85] Successfully initialized EGL. Major : 1 Minor: 5
I0000 00:00:1762258728.885121   92197 gl_context.cc:369] GL version: 3.2 (OpenGL ES 3.2 Mesa 25.0.7-0ubuntu0.24.04.1), renderer: AMD Radeon Graphics (radeonsi, renoir, ACO, DRM 3.61, 6.14.0-33-generic)
W0000 00:00:1762258728.954507   92179 inference_feedback_manager.cc:114] Feedback manager requires a model with a single signature inference. Disabling support for feedback tensors.
W0000 00:00:1762258729.002143   92191 inference_feedback_manager.cc:114] Feedback manager requires a model with a single signature inference. Disabling support for feedback tensors.


Done 069371f5-6570-4e19-aaf4-a53e9a7f91d1.jpg: Right рука
Done 831058d5-58d1-4910-b41d-2e91d98bf816.jpg: Right рука
   Hands are not found in 004182a8-96fb-4fc1-9c3d-bfe4f8b8246d.jpg
Done d24a0b9e-b9be-455b-ab68-ee6ba480abdb.jpg: Left рука
Done 4318db05-2c3e-4d08-a92a-93e1fdcdd616.jpg: Right рука
   Hands are not found in 39642771-a2aa-49ae-ae50-8f07afd915f0.jpg
Done a8c23f66-b3db-4011-a1cf-249a0a03956a.jpg: Right рука
Done 27292f18-88f7-4909-9f22-29a33bcd142b.jpg: Right рука
   Hands are not found in 1127e3f0-2a0f-4697-a630-b637949be2a8.jpg
Done 61a29820-30d7-4a15-8d65-459d973d15fd.jpg: Left рука
Done 37142719-7595-42c4-91c8-9b1b1f0adc1d.jpg: Left рука
Done 1188ac6f-8f5e-4b0a-82ae-3dc91b2472ab.jpg: Right рука
Done eef861a3-321a-4ecb-8e9a-263651974c70.jpg: Right рука
Done 504a89a3-44b8-4d04-90e3-ac1692439d05.jpg: Right рука
Done a9590585-ac31-4015-b500-b7d25ff06f41.jpg: Left рука
Done 3e8f97e6-0ad5-45c9-8495-9bc5ba9a445f.jpg: Left рука
   Hands are not found in bc79bc51-c36b-4698-b5b1-

In [8]:
# dislike --> mafia
output_csv = '../data/raw/mafia.csv'

extract_single_hand_to_csv(images_folder='/home/fateee/Desktop/ulyana/hagrid/super_bolshoy_dataset/dislike', 
                         output_csv=output_csv, 
                         gesture_label='mafia')

I0000 00:00:1762263095.592625   47693 gl_context_egl.cc:85] Successfully initialized EGL. Major : 1 Minor: 5
I0000 00:00:1762263095.604032   97582 gl_context.cc:369] GL version: 3.2 (OpenGL ES 3.2 Mesa 25.0.7-0ubuntu0.24.04.1), renderer: AMD Radeon Graphics (radeonsi, renoir, ACO, DRM 3.61, 6.14.0-33-generic)
W0000 00:00:1762263095.666625   97568 inference_feedback_manager.cc:114] Feedback manager requires a model with a single signature inference. Disabling support for feedback tensors.
W0000 00:00:1762263095.691494   97572 inference_feedback_manager.cc:114] Feedback manager requires a model with a single signature inference. Disabling support for feedback tensors.


Done a3c31f21-22e7-4e92-84d3-700e9f3bbcf0.jpg: Left рука
Done 7e4fee4f-b5cc-4f17-a972-bfb719c6af12.jpg: Left рука
Done 49850024-26ed-49ee-84a6-a8dd01b06229.jpg: Right рука
Done 5e9d42c2-c07e-4fb6-b476-7ea6f2c2cd04.jpg: Left рука
Done 6e513955-cc94-48f2-af0e-298fb91c0fac.jpg: Left рука
Done fbf84907-5e3e-458e-b525-f3d693a21f31.jpg: Left рука
Done c17b6cf0-f4fc-4047-bf0c-69adc337f8d1.jpg: Right рука
Done 9bfcb7c4-8e6f-47c9-93bf-ce6b23d92741.jpg: Left рука
   Hands are not found in 54fd4db6-4123-453d-89cc-5ef454a25295.jpg
Done f273a193-44c0-41e9-aa6c-6533a044ba1e.jpg: Right рука
Done d0310fb8-a301-405a-87b1-d62a2398b60b.jpg: Right рука
   Hands are not found in c2187477-58d7-4d28-b0e2-2d64e7a3fc63.jpg
Done f4122d2a-4f40-4029-b878-e5e2bf4cf57b.jpg: Right рука
   Hands are not found in 6511b137-06d2-4577-8673-22c3a9e69b59.jpg
   Hands are not found in a106ef9b-e030-4344-8f27-c39f2b2b0335.jpg
Done 8b9b59b3-e6e7-46cc-8378-81e9d30f0665.jpg: Left рука
Done 72460915-ed61-4a99-a775-ee24d7151733.j

In [11]:
# dislike --> mafia
output_csv = '../data/raw/mafia.csv'

extract_single_hand_to_csv(images_folder='/home/fateee/Desktop/ulyana/hagrid/super_bolshoy_dataset/', 
                         output_csv=output_csv, 
                         gesture_label='mafia')

I0000 00:00:1762265649.349433   47693 gl_context_egl.cc:85] Successfully initialized EGL. Major : 1 Minor: 5
I0000 00:00:1762265649.351901  103593 gl_context.cc:369] GL version: 3.2 (OpenGL ES 3.2 Mesa 25.0.7-0ubuntu0.24.04.1), renderer: AMD Radeon Graphics (radeonsi, renoir, ACO, DRM 3.61, 6.14.0-33-generic)
W0000 00:00:1762265649.391008  103575 inference_feedback_manager.cc:114] Feedback manager requires a model with a single signature inference. Disabling support for feedback tensors.
W0000 00:00:1762265649.423938  103580 inference_feedback_manager.cc:114] Feedback manager requires a model with a single signature inference. Disabling support for feedback tensors.


Done 0a0d4922-d6af-474b-80be-95cca60278c3.jpg: Left рука

CSV saved: ../data/raw/mafia.csv (20912 rows)
Total images processed: 1
Images with detected hand(s): 1
Images where no hand was detected: 0
Success rate: 100.0%
